# Exercise 1

In [39]:
import nltk
from nltk import word_tokenize, pos_tag

## Classifiers
note: for model1 and model3 you can try different classifiers: Hidden Markov Model, Logistic Regression, Maximum Entropy Markov Models, Decision Trees, Naive Bayes, etc.. __choose one!__

In [40]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.feature_extraction import DictVectorizer
from sklearn.pipeline import Pipeline

### 1. model1 = your POS tagger model (english)

In [41]:
def features(sentence, index):
    return {
        'word': sentence[index],
        'length': len(sentence[index]),
        'is_capitalized': sentence[index][0].upper() == sentence[index][0],
        'prefix-1': sentence[index][0],
        'suffix-1': sentence[index][-1],
        'prev_word': '' if index == 0 else sentence[index - 1],
        'next_word': '' if index == len(sentence) - 1 else sentence[index + 1]
    }

print(features("halli hallo i bims der Programmierer".strip().split(" "), 3))

{'word': 'bims', 'length': 4, 'is_capitalized': False, 'prefix-1': 'b', 'suffix-1': 's', 'prev_word': 'i', 'next_word': 'der'}


### 2. model2 = pre-trained POS tagger model using NLTK (maxentropy english)


### 3. model3.x = rule-based classifiers (x = 1 to 5)

### 4. model4 = your POS tagger model (not english)

### 5. model5 = pre-trained POS tagger model using RDRPOSTagger 1 or TreeTagger 2 (not english)

## Corpora
note: data split for training/test = 0.8/0.2 (sequencial)

#### 1. X1 = nltk.corpus.treebank (english)

In [42]:
nltk.download('treebank')
x1 = nltk.corpus.treebank

[nltk_data] Downloading package treebank to
[nltk_data]     /Users/Carsten/nltk_data...
[nltk_data]   Package treebank is already up-to-date!


#### 2. X2 = nltk.corpus.brown (english)

In [43]:
nltk.download('brown')
x2 = nltk.corpus.brown

[nltk_data] Downloading package brown to /Users/Carsten/nltk_data...
[nltk_data]   Package brown is already up-to-date!


#### 3. X3 = other language (not english)

In [44]:
#nltk.download('brown')
#x3 = other language

### Task 1
* get results for english (plot a graph with all classifiers x results)
    * performance 1.1 = model1 in X1
    * performance 1.2 = model2 in X1
    * performance 1.3.x = model3.x in X1
    * performance 1.4 = model1 in X2
    * performance 1.5 = model2 in X2
    * performance 1.6.x = model3.x in X2

##### Generate Training and Testdata for X1
1. split annotaed sentences into training and testdata
2. split trainingdata into input data and teacherdata
    *input is the feature vector of each word
    *output is a list of POS tags for each word and sentences

In [45]:
#to generate trainingsdata, delete the assigned tags as a function
def untag(tagged_sentence):
    return [w for w, t in tagged_sentence]

In [46]:
#object including the annotated sentences
annotated_sent = nltk.corpus.treebank.tagged_sents()

#to split the data, calculate the borders for ratio
cutoff = int(.8 * len(annotated_sent))
training_sentences_X1 = annotated_sent[:cutoff]
test_sentences_X1 = annotated_sent[cutoff:]

#show the amount of sentences
print("got ",len(training_sentences_X1)," training sentences and ", len(test_sentences_X1), " test sentences")

got  3131  training sentences and  783  test sentences


In [47]:
#for training split sentences with its tags into y (for a sentences its resulting tags for each word) and transform sentences and x as a list of the features extracet for echt word in the sentences
def transform_to_dataset(tagged_sentences):
    X, y = [], []
    for tagged_sentence in tagged_sentences:
        for index in range(len(tagged_sentence)):
            X.append(features(untag(tagged_sentence), index))
            y.append(tagged_sentence[index][1]) 
    return X, y

In [48]:
#trainings inputset X and training teacher set y
X1, y1 = transform_to_dataset(training_sentences_X1)

##### Generate Training and Testdata for X2
1. split annotaed sentences into training and testdata
2. split trainingdata into input data and teacherdata
    *input is the feature vector of each word
    *output is a list of POS tags for each word and sentences

In [49]:
#object including the annotated sentences
annotated_sent = nltk.corpus.brown.tagged_sents()

#to split the data, calculate the borders for ratio
cutoff = int(.8 * len(annotated_sent))
training_sentences_X2 = annotated_sent[:cutoff]
test_sentences_X2 = annotated_sent[cutoff:]

#show the amount of sentences
print("got ",len(training_sentences_X2)," training sentences and ", len(test_sentences_X2), " test sentences")

got  45872  training sentences and  11468  test sentences


In [50]:
#trainings inputset X and training teacher set y
X2, y2 = transform_to_dataset(training_sentences_X2)

#### Implementing a classifier
relevant imports
* decision tree as the AI for classfing
* dict vercorizer transforms the feature dictionary into a vector as the input for the tree

In [51]:
from sklearn.tree import DecisionTreeClassifier
from sklearn.feature_extraction import DictVectorizer
from sklearn.pipeline import Pipeline

Pipeline manages vectorizer and classifier

In [52]:
clf = Pipeline([
    ('vectorizer', DictVectorizer(sparse=False)),
    ('classifier', DecisionTreeClassifier(criterion='entropy'))
])

##### Calculate performance 1.1 
* fit the decision tree for a limited amount (size) of training 
* test data and compare with score function on testdata

In [53]:
size=10000
clf.fit(X[:size], y[:size])
 
print('training OK')
 
X1_test, y1_test = transform_to_dataset(test_sentences_X1)

performance1_1 = clf.score(X1_test, y1_test)

print("Accuracy:", performance1_1)

training OK
Accuracy: 0.87983432307


##### Calculate other performances

In [58]:
performance1_2 = 0

performance1_3 = 0

# performance1_4
size=10000
clf.fit(X2[:size], y2[:size])
X2_test, y2_test = transform_to_dataset(test_sentences_X2)
performance1_4 = clf.score(X2_test, y2_test)
print("calculated perfomance 1.4= ",performance1_4)

performance1_5 = 0

performance1_6 = 0

calculated perfomance 1.4=  0.756485959481


#### Using the classifier
for results the link of pos_tags:
https://www.ling.upenn.edu/courses/Fall_2003/ling001/penn_treebank_pos.html

In [56]:
def pos_tag(sentence):
    print('checking...')
    tagged_sentence = []
    tags = clf.predict([features(sentence, index) for index in range(len(sentence))])
    return zip(sentence, tags)

import platform
print(platform.python_version())

print(list(pos_tag(word_tokenize('Hello world, lets do something awesome today!'))))

3.6.3
checking...
[('Hello', 'CS'), ('world', 'NN'), (',', ','), ('lets', 'NNS'), ('do', 'DO'), ('something', 'PN'), ('awesome', 'NN'), ('today', 'NR'), ('!', 'CD')]


### Results for Task 1
* get results for english (plot a graph with all classifiers x results)
    * performance 1.1 = model1 in X1
    * performance 1.2 = model2 in X1
    * performance 1.3.x = model3.x in X1
    * performance 1.4 = model1 in X2
    * performance 1.5 = model2 in X2
    * performance 1.6.x = model3.x in X2

In [57]:
import plotly
plotly.tools.set_credentials_file(username='carsten95', api_key='vElf5IOxiFheQdjTxjXW')
plotly.__version__
import plotly.plotly as py
import plotly.graph_objs as go

data = [go.Bar(
            x=['performance 1.1', 'performance 1.2', 'performance 1.3', 'performance 1.4', 'performance 1.5' , 'performance 1.6'],
            y=[performance1_1, performance1_2, performance1_3, performance1_4, performance1_5, performance1_6]
    )]

py.iplot(data, filename='basic-bar')

High five! You successfully sent some data to your account on plotly. View your plot in your browser at https://plot.ly/~carsten95/0 or inside your plot.ly account where it is named 'basic-bar'


### Results for Task 2
* train your model with standard features (plot a graph with all classifiers x results)
    * performance 2.1 = model4 in X3
    * performance 2.2 = model5 in X3

In [60]:
performance2_1 = 0
performance2_2 = 0

data = [go.Bar(
            x=['performance 2.1', 'performance 2.2'],
            y=[performance2_1, performance2_2]
    )]

py.iplot(data, filename='basic-bar')

High five! You successfully sent some data to your account on plotly. View your plot in your browser at https://plot.ly/~carsten95/0 or inside your plot.ly account where it is named 'basic-bar'
